In [9]:
import pandas as pd

train_df = pd.read_csv('../data/train/wikisql_train.csv')

train_df = train_df[train_df['sql'].apply(lambda x: len(x.split()) < 10)].reset_index()

train_df.shape

(17922, 7)

In [10]:
train_df

index                                           question  \
0          2            What is the format for South Australia?   
1          6   who is the manufacturer for the order year 1998?   
2          7               how many times is the model ge40lfr?   
3         10       What if the description of a ch-47d chinook?   
4         12         What school did player number 6 come from?   
...      ...                                                ...   
17917  56339          What percentage did chris wright receive?   
17918  56347  What is the high total for players with over 1...   
17919  56350  What time was the match played with a score of...   
17920  56351     On which ground did the team play Aston Villa?   
17921  56354        Which report includes a Circuit of Tripoli?   

                                                     sql  \
0      SELECT Format FROM table WHERE State/territory...   
1      SELECT Manufacturer FROM table WHERE Order Yea...   
2      SELECT COUNT Manufacturer FROM table WHERE Mod...   
3      SELECT Description FROM table WHERE Aircraft =...   
4       SELECT School/Club Team FROM table WHERE No. = 6   
...                                                  ...   
17917  SELECT Percentage FROM table WHERE Candidate =...   
17918        SELECT MAX Total FROM table WHERE Solo > 15   
17919           SELECT Time FROM table WHERE Score = 3-2   
17920  SELECT Ground FROM table WHERE Opponent = asto...   
17921   SELECT Report FROM table WHERE Circuit = tripoli   

                                            table_header  \
0      ['State/territory', 'Text/background colour', ...   
1      ['Order Year', 'Manufacturer', 'Model', 'Fleet...   
2      ['Order Year', 'Manufacturer', 'Model', 'Fleet...   
3      ['Aircraft', 'Description', 'Max Gross Weight'...   
4      ['Player', 'No.', 'Nationality', 'Position', '...   
...                                                  ...   
17917  ['Year', 'Office', 'Candidate', 'Popular Votes...   
17918  ['Player', 'Solo', 'Total', 'Sacks', 'Fumble f...   
17919  ['Date', 'Time', 'Competition', 'Opponent', 'G...   
17920  ['Date', 'Time', 'Competition', 'Opponent', 'G...   
17921  ['Name', 'Circuit', 'Date', 'Winning driver', ...   

                                     table_header_types                conds  \
0      ['text', 'text', 'text', 'text', 'text', 'text']  ['South Australia']   
1      ['text', 'text', 'text', 'text', 'text', 'text']             ['1998']   
2      ['text', 'text', 'text', 'text', 'text', 'text']          ['GE40LFR']   
3              ['text', 'text', 'text', 'text', 'text']   ['CH-47D Chinook']   
4      ['text', 'text', 'text', 'text', 'text', 'text']                ['6']   
...                                                 ...                  ...   
17917          ['real', 'text', 'text', 'real', 'text']     ['chris wright']   
17918  ['text', 'real', 'real', 'text', 'real', 'real']               ['15']   
17919  ['text', 'text', 'text', 'text', 'text', 'text']              ['3-2']   
17920  ['text', 'text', 'text', 'text', 'text', 'text']      ['aston villa']   
17921  ['text', 'text', 'text', 'text', 'text', 'text']          ['tripoli']   

                                                    rows  
0      [['Australian Capital Territory', 'blue/white'...  
1      [['1992-93', 'Gillig', 'Phantom (High Floor)',...  
2      [['1992-93', 'Gillig', 'Phantom (High Floor)',...  
3      [['Robinson R-22', 'Light utility helicopter',...  
4      [['Quincy Acy', '4', 'United States', 'Forward...  
...                                                  ...  
17917  [['1988', 'US Senator', 'Derrick Grimmer', '9,...  
17918  [['Anthony Gebhart', '15', '31', '0', '0', '0'...  
17919  [['17 July 2007', '15:30 GMT', 'Friendly Match...  
17920  [['17 July 2007', '15:30 GMT', 'Friendly Match...  
17921  [['Tripoli Grand Prix', 'Tripoli', '11 March',...  

[17922 rows x 7 columns]

In [34]:
train_df = train_df[train_df['sql'].apply(lambda x: len(x.split()) < 10)].reset_index()

train_df.shape

(17922, 8)

In [35]:
import tiktoken

In [36]:
print(f'gpt2: {tiktoken.get_encoding("gpt2").n_vocab}')

print(f'r50k_base {tiktoken.get_encoding("r50k_base").n_vocab}')
      
print(f'p50k_base: {tiktoken.get_encoding("p50k_base").n_vocab}')
print(f'p50k_edit: {tiktoken.get_encoding("p50k_edit").n_vocab}')
print(f'cl100k_base: {tiktoken.get_encoding("cl100k_base").n_vocab}')



    # "r50k_base": r50k_base,
    # "p50k_base": p50k_base,
    # "p50k_edit": p50k_edit,
    # "cl100k_base": cl100k_base,)

gpt2: 50257
r50k_base 50257
p50k_base: 50281
p50k_edit: 50284
cl100k_base: 100277


In [62]:
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Embedding, LSTM, Dense, Attention, Masking, Concatenate
from tensorflow.keras.losses import SparseCategoricalCrossentropy

MAX_LEN = 20
enc = tiktoken.get_encoding('gpt2')
vocab_size = enc.n_vocab
PADD_VALUE = -1
def preprocessing(column:pd.DataFrame,padd_val:int=-1):

    sequences = []
    for sent in column:
        print(enc.encode(sent))
        sequences.append(enc.encode(sent))
    padded = pad_sequences(sequences, padding='post',value=padd_val,maxlen=MAX_LEN)
    return padded


padded_question = preprocessing(train_df['question'])
padded_context = preprocessing(train_df['table_header'])
padded_sql = preprocessing(train_df['sql'])


print(f"padded_question shape: {padded_question.shape}")
print(f"padded_context shape: {padded_context.shape}")
print(f"padded_sql {padded_sql.shape}")
    

[2061, 318, 262, 5794, 329, 2520, 4505, 30]
[8727, 318, 262, 11554, 329, 262, 1502, 614, 7795, 30]
[4919, 867, 1661, 318, 262, 2746, 4903, 1821, 1652, 81, 30]
[2061, 611, 262, 6764, 286, 257, 442, 12, 2857, 67, 22531, 566, 30]
[2061, 1524, 750, 2137, 1271, 718, 1282, 422, 30]
[2061, 2292, 750, 262, 2137, 422, 28245, 711, 30]
[13828, 1271, 373, 9925, 440, 6, 33, 563, 415, 30]
[13828, 2292, 857, 32035, 16483, 711, 30]
[13828, 1499, 318, 262, 2137, 326, 1816, 284, 31393, 422, 30]
[2061, 338, 23617, 20920, 29835, 30]
[4758, 2137, 318, 422, 4903, 2398, 544]
[10919, 2292, 750, 262, 2137, 422, 2018, 13554, 711]
[2061, 29835, 318, 262, 2137, 337, 6837, 1837, 21555, 947, 30]
[2215, 262, 1266, 5461, 373, 309, 3388, 11, 703, 867, 661, 1625, 287, 362, 358, 30]
[2061, 640, 373, 262, 4511, 329, 362, 358, 957, 39116, 30]
[2215, 750, 262, 12477, 30783, 423, 511, 717, 36595, 286, 262, 6280, 8464, 30]
[2061, 4152, 750, 262, 36595, 286, 262, 6280, 422, 262, 14939, 17652, 5262, 30]
[2061, 318, 262, 18548,

In [63]:
train_df[['question'][0]]

0                  What is the format for South Australia?
1         who is the manufacturer for the order year 1998?
2                     how many times is the model ge40lfr?
3             What if the description of a ch-47d chinook?
4               What school did player number 6 come from?
                               ...                        
17917            What percentage did chris wright receive?
17918    What is the high total for players with over 1...
17919    What time was the match played with a score of...
17920       On which ground did the team play Aston Villa?
17921          Which report includes a Circuit of Tripoli?
Name: question, Length: 17922, dtype: object

In [64]:
# Model architecture
embedding_dim = 128
units = 128


# Input layers
input_question = Input(shape=(MAX_LEN,))
input_context = Input(shape=(MAX_LEN,))

# Embedding layers
embedding_layer_question = Embedding(input_dim=vocab_size, output_dim=embedding_dim, mask_zero=True)(input_question)
embedding_layer_context = Embedding(input_dim=vocab_size, output_dim=embedding_dim, mask_zero=True)(input_context)

# LSTM layers
lstm_layer_question = LSTM(units, return_sequences=True)(embedding_layer_question)
lstm_layer_context = LSTM(units, return_sequences=True)(embedding_layer_context)

# Attention layer
attention = Attention()([lstm_layer_question, lstm_layer_context])

# Concatenate the attention output with the LSTM output for context
context_combined = Concatenate(axis=-1)([lstm_layer_context, attention])

# Output layer
output_layer = Dense(vocab_size, activation='softmax')(context_combined)




In [65]:
# Model
model = Model(inputs=[input_question, input_context], outputs=output_layer)
model.compile(optimizer='adam', loss=SparseCategoricalCrossentropy(), metrics=['accuracy'])

# Split the data into train and test sets
# X_train, X_test, y_train, y_test = train_test_split([padded_question[0:100], padded_context[0:100]], padded_sql[0:100], test_size=0.2, random_state=42)



In [67]:
# Train the model
history = model.fit([padded_question,padded_context], padded_sql, epochs=15, batch_size=64, validation_split=0.2)

Epoch 1/15
225/225 [==============================] - ETA: 0s - loss: 4.2475 - accuracy: 0.3737

W0000 00:00:1707357448.855611       1 op_level_cost_estimator.cc:699] Error in PredictCost() for the op: op: "Softmax" attr { key: "T" value { type: DT_FLOAT } } inputs { dtype: DT_FLOAT shape { unknown_rank: true } } device { type: "CPU" model: "0" frequency: 2400 num_cores: 8 environment { key: "cpu_instruction_set" value: "ARM NEON" } environment { key: "eigen" value: "3.4.90" } l1_cache_size: 16384 l2_cache_size: 524288 l3_cache_size: 524288 memory_size: 268435456 } outputs { dtype: DT_FLOAT shape { unknown_rank: true } }


225/225 [==============================] - 177s 786ms/step - loss: 4.2475 - accuracy: 0.3737 - val_loss: 4.0380 - val_accuracy: 0.3998
Epoch 2/15
225/225 [==============================] - 188s 834ms/step - loss: 3.8157 - accuracy: 0.4372 - val_loss: 3.8367 - val_accuracy: 0.4570
Epoch 3/15
225/225 [==============================] - 196s 871ms/step - loss: 3.6058 - accuracy: 0.4668 - val_loss: 3.7141 - val_accuracy: 0.4666
Epoch 4/15
225/225 [==============================] - 192s 854ms/step - loss: 3.4111 - accuracy: 0.4815 - val_loss: 3.6364 - val_accuracy: 0.4736
Epoch 5/15
225/225 [==============================] - 179s 796ms/step - loss: 3.2508 - accuracy: 0.4979 - val_loss: 3.5416 - val_accuracy: 0.4806
Epoch 6/15
225/225 [==============================] - 177s 785ms/step - loss: 3.1050 - accuracy: 0.5119 - val_loss: 3.4838 - val_accuracy: 0.4825
Epoch 7/15
225/225 [==============================] - 169s 749ms/step - loss: 2.9576 - accuracy: 0.5240 - val_loss: 3.4779 - val_accura

In [ ]:
def generate_sql(question,context,padding_index = 0):

    question_sequence = enc.encode(question)
    # print(f"question_sequence: {question_sequence}")
    question_padded = pad_sequences([question_sequence], padding='post',maxlen=MAX_LEN)

    context_sequence = enc.encode(context)
    context_padded = pad_sequences([question_sequence], padding='post',maxlen=MAX_LEN)
    # print(f"question_padded: {question_padded}")
    predicted_sequence = model.predict([question_padded,context_padded])
    # print(f"predicted_sequence: {predicted_sequence}")
    predicted_indices = np.argmax(predicted_sequence, axis=-1)
    predicted_indices[predicted_sequence.argmax(axis=-1) == padding_index] = padding_index
    predicted_query = enc.decode(predicted_indices[0])
    # predicted_sql_query = enc.decode(predicted_sequence)
    return predicted_query

In [61]:
for i in range(11,24):
    input_question = train_df.loc[i,'question']
    input_context = train_df.loc[i,'table_header']
    actual_query = train_df.loc[i,'sql']

    input_question,input_context


    predicted_query = generate_sql(question=input_question, context=input_context)

    print(f"actual query: {actual_query}\n")
    print(f"predicted query: {predicted_query}")
    print(f"length of predictd query: {len(predicted_query.split(' '))}")

1/1 [==============================] - 0s 49ms/step
actual query: SELECT Position FROM table WHERE School/Club Team = Connecticut

predicted query: SELECTSELECTSELECTSELECT Date!!!!!!!!!!!!!!!
length of predictd query: 2
1/1 [==============================] - 0s 22ms/step
actual query: SELECT Nationality FROM table WHERE Player = Muggsy Bogues

predicted query: SELECTSELECTSELECT Date Date!!!!!!!!!!!!!!!
length of predictd query: 3
1/1 [==============================] - 0s 20ms/step
actual query: SELECT 2nd FROM table WHERE Best finish = T69

predicted query: SELECTSELECTSELECTSELECTSELECT MIN FROM table WHERE WHERE = =!!!!!!!!
length of predictd query: 8
1/1 [==============================] - 0s 19ms/step
actual query: SELECT MAX 2nd FROM table

predicted query: SELECTSELECT COUNT FROM FROM FROM = =  !!!!!!!!!!
length of predictd query: 9
1/1 [==============================] - 0s 18ms/step
actual query: SELECT MIN Season FROM table WHERE Team = MetroStars

predicted query: SELECTSELEC

In [ ]:
class PredictTiktoken():
    
    def __init__(self,model):
        self.model = model

    def inference_prediction(self,input_question:str,input_context:str ,padding_index=0) -> str:
        question_sequence = enc.encode(input_question)
        # print(f"question_sequence: {question_sequence}")
        question_padded = pad_sequences([question_sequence], padding='post',maxlen=MAX_LEN)

        context_sequence = enc.encode(input_context)
        context_padded = pad_sequences([question_sequence], padding='post',maxlen=MAX_LEN)
        # print(f"question_padded: {question_padded}")
        predicted_sequence = model.predict([question_padded,context_padded])
        # print(f"predicted_sequence: {predicted_sequence}")
        predicted_indices = np.argmax(predicted_sequence, axis=-1)
        predicted_indices[predicted_sequence.argmax(axis=-1) == padding_index] = padding_index
        predicted_query = enc.decode(predicted_indices[0])
        # predicted_sql_query = enc.decode(predicted_sequence)
        return predicted_query
            
    
    def batch_prediction(self, X_val: pd.DataFrame, y_val: pd.DataFrame):
        pred_queries = []
        true_queries = []
        for i in range(len(X_val)):
            question = X_val.loc[i, "question"]
            context =  X_val.loc[i, "table_header"]
            predicted_query = self.inference_prediction(question,context)
            pred_queries.append(predicted_query)
            true_queries.append(y_val.loc[i, 'sql'])

        return true_queries, pred_queries


In [ ]:
from nltk.translate.bleu_score import sentence_bleu,SmoothingFunction

def evaluate(X_val: pd.DataFrame, y_val: pd.DataFrame):
        smoothing_function = SmoothingFunction().method1
        y_test, decoded_predictions = PredictTiktoken(model).batch_prediction(X_val, y_val)
        bleu_scores = [sentence_bleu([true_query.split()], generated_query.split(),smoothing_function=smoothing_function) for true_query, generated_query in zip(y_test, decoded_predictions)]
        return bleu_scores


score = evaluate(X_val,y_val)
average_score = sum(score) /len(score)
print(average_score)



In [ ]:
from rouge import Rouge

def evaluate_sql_to_text_rouge(X_val, y_val):
    """
    Evaluate the SQL-to-text model using ROUGE score.

    Args:
    - model: The trained SQL-to-text model.
    - X_val: Validation set of SQL queries.
    - y_val: Reference texts for evaluation.

    Returns:
    - ROUGE-N score.
    """
    rouge = Rouge()
    rouge_scores = []

    for i in range(len(X_val)):
        predicted_sql = generate_sql(X_val.loc[i, 'question'], X_val.loc[i, 'table_header'])
        reference_text = y_val.loc[i, 'sql']  # Assuming 'text' is the reference column

        # Calculate ROUGE scores
        scores = rouge.get_scores(predicted_sql, reference_text)
        # print(f"score: {scores}")

        rouge_score = scores[0]['rouge-l']['f']

        # print(f"rouge_score: {rouge_score}")


        rouge_scores.append(rouge_score)

    # Calculate the average ROUGE score
    avg_rouge_score = sum(rouge_scores) / len(rouge_scores)

    return avg_rouge_score

# Example usage:
# avg_rouge = evaluate_sql_to_text_rouge(model, X_validation, y_validation)
# print(f"Average ROUGE-2 Score: {avg_rouge}")
evaluate_sql_to_text_rouge(X_val=X_val,y_val=y_val)